In [1]:
! pyspark --version

24/08/23 23:21:04 WARN Utils: Your hostname, ahmad-HP-ZBook-17 resolves to a loopback address: 127.0.1.1; using 192.168.1.35 instead (on interface wlo1)
24/08/23 23:21:04 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Welcome to
      ____              __
     / __/__  ___ _____/ /__
    _\ \/ _ \/ _ `/ __/  '_/
   /___/ .__/\_,_/_/ /_/\_\   version 3.5.2
      /_/
                        
Using Scala version 2.12.18, OpenJDK 64-Bit Server VM, 11.0.24
Branch HEAD
Compiled by user ubuntu on 2024-08-06T11:36:15Z
Revision bb7846dd487f259994fdc69e18e03382e3f64f42
Url https://github.com/apache/spark
Type --help for more information.


In [ ]:
! pip install Spark-df-Cleaner

In [2]:
from pyspark.sql import SparkSession
from pyspark.sql.types import StringType, LongType
import os
from SparkCleaner import *

In [3]:
spark = SparkSession.builder.appName("DQ").getOrCreate()

24/08/23 23:21:46 WARN Utils: Your hostname, ahmad-HP-ZBook-17 resolves to a loopback address: 127.0.1.1; using 192.168.1.35 instead (on interface wlo1)
24/08/23 23:21:46 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/08/23 23:21:51 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [10]:
spark.conf.set("spark.sql.legacy.timeParserPolicy","LEGACY")

In [11]:
df = spark.read.option("header", True) \
    .option("inferSchema", True) \
    .csv("./test_data/Amazon Sale Report.csv").drop('index')
    
new_columns = [col.replace(" ", "_").replace("-", "_") for col in df.columns]
df = df.toDF(*new_columns)
df.show()

+-------------------+----------+--------------------+----------+-------------+------------------+--------+----+--------------+---+--------+------+-----------+--------------+----------------+------------+-----+------------+----+--------+
|           Order_ID|      Date|              Status|Fulfilment|Sales_Channel|ship_service_level|Category|Size|Courier_Status|Qty|currency|Amount|  ship_city|    ship_state|ship_postal_code|ship_country|  B2B|fulfilled_by| New|PendingS|
+-------------------+----------+--------------------+----------+-------------+------------------+--------+----+--------------+---+--------+------+-----------+--------------+----------------+------------+-----+------------+----+--------+
|405-8078784-5731545|0006-06-22|           Cancelled|  Merchant|    Amazon.in|          Standard| T-shirt|   S|    On the Way|  0|     INR|647.62|     MUMBAI|   MAHARASHTRA|          400081|          IN|false|   Easy Ship|NULL|    NULL|
|171-9198151-1101146|0006-06-22|Shipped - Deliver...

In [12]:
cleaning_strategies=[
    DropMissingValuesStrategy(columns=['Qty', 'Amount', 'Order_ID', 'Date', 'currency']),
    FilterNegativeValuesStrategy(columns=['Qty', 'Amount']),
    ValidateDatesStrategy(columns=['Date'], date_format="MM-dd-yy"),
    DropDuplicatesStrategy(columns=['Order_ID'])
]
cleaner = CleaningPipeline()
cleaner.set_dataframe(df=df)
cleaner.add_strategy(cleaning_strategies)
clean_df = cleaner.run()
clean_df.show()

24/08/23 23:26:45 WARN WindowExec: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
24/08/23 23:26:45 WARN WindowExec: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
24/08/23 23:26:46 WARN WindowExec: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
24/08/23 23:26:47 WARN WindowExec: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
24/08/23 23:26:47 WARN WindowExec: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
24/08/23 23:26:48 WARN WindowExec: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
24/08/23 2

+-------------------+----------+--------------------+----------+-------------+------------------+--------+----+--------------+---+--------+------+--------------------+--------------+----------------+------------+-----+------------+----+--------+
|           Order_ID|      Date|              Status|Fulfilment|Sales_Channel|ship_service_level|Category|Size|Courier_Status|Qty|currency|Amount|           ship_city|    ship_state|ship_postal_code|ship_country|  B2B|fulfilled_by| New|PendingS|
+-------------------+----------+--------------------+----------+-------------+------------------+--------+----+--------------+---+--------+------+--------------------+--------------+----------------+------------+-----+------------+----+--------+
|171-0005741-2261112|0008-05-22|             Shipped|    Amazon|    Amazon.in|         Expedited|   Shirt|  XS|       Shipped|  1|     INR| 558.0|           HYDERABAD|     TELANGANA|          500072|          IN|false|        NULL|NULL|    NULL|
|171-0005999-318

# Getting cleaning report

In [15]:
report = cleaner.get_report()
print(report)

{
    "DropMissingValuesStrategy": [
        {
            "index": 9,
            "column": "Amount",
            "error_type": "missing_value: None"
        },
        {
            "index": 30,
            "column": "Amount",
            "error_type": "missing_value: None"
        },
        {
            "index": 66,
            "column": "Amount",
            "error_type": "missing_value: None"
        },
        {
            "index": 85,
            "column": "Amount",
            "error_type": "missing_value: None"
        },
        {
            "index": 96,
            "column": "Amount",
            "error_type": "missing_value: None"
        },
        {
            "index": 102,
            "column": "Amount",
            "error_type": "missing_value: None"
        },
        {
            "index": 133,
            "column": "Amount",
            "error_type": "missing_value: None"
        },
        {
            "index": 140,
            "column": "Amount",
            

In [20]:
import json
json_data = json.loads(report)
report_df = spark.read.json(spark.sparkContext.parallelize([json_data]))
report_df.show()


24/08/23 23:33:44 WARN TaskSetManager: Stage 87 contains a task of very large size (4722 KiB). The maximum recommended task size is 1000 KiB.
24/08/23 23:33:45 WARN TaskSetManager: Stage 90 contains a task of very large size (4722 KiB). The maximum recommended task size is 1000 KiB.


+----------------------+-------------------------+----------------------------+---------------------+
|DropDuplicatesStrategy|DropMissingValuesStrategy|FilterNegativeValuesStrategy|ValidateDatesStrategy|
+----------------------+-------------------------+----------------------------+---------------------+
|  [{[Order_ID], Dup...|     [{Amount, missing...|        [{Qty, negative_v...|                   []|
+----------------------+-------------------------+----------------------------+---------------------+



In [22]:
strategies_dfs = {}
for strategy_name, records in json_data.items():
    try:
        strategies_dfs[strategy_name] = spark.createDataFrame(records)
    except Exception as e:
        print(f"ERROR OCCURED: dataframe for: {strategy_name}, error:{e}")

print(strategies_dfs.keys())
        

ERROR OCCURED: dataframe for: ValidateDatesStrategy, error:[CANNOT_INFER_EMPTY_SCHEMA] Can not infer schema from empty dataset.
dict_keys(['DropMissingValuesStrategy', 'FilterNegativeValuesStrategy', 'DropDuplicatesStrategy'])


In [24]:
# Accessing Drop Missing Values
drop_m_df = strategies_dfs['DropDuplicatesStrategy']
drop_m_df.count()

7880

In [25]:
# accessing duplicates
drop_d_df = strategies_dfs['DropDuplicatesStrategy']
drop_d_df.show()

+----------+--------------------+-----+
|    column|          error_type|index|
+----------+--------------------+-----+
|[Order_ID]|Duplicate row fou...|   39|
|[Order_ID]|Duplicate row fou...|   63|
|[Order_ID]|Duplicate row fou...|   81|
|[Order_ID]|Duplicate row fou...|   82|
|[Order_ID]|Duplicate row fou...|  107|
|[Order_ID]|Duplicate row fou...|  118|
|[Order_ID]|Duplicate row fou...|  119|
|[Order_ID]|Duplicate row fou...|  124|
|[Order_ID]|Duplicate row fou...|  168|
|[Order_ID]|Duplicate row fou...|  202|
|[Order_ID]|Duplicate row fou...|  203|
|[Order_ID]|Duplicate row fou...|  205|
|[Order_ID]|Duplicate row fou...|  206|
|[Order_ID]|Duplicate row fou...|  207|
|[Order_ID]|Duplicate row fou...|  208|
|[Order_ID]|Duplicate row fou...|  209|
|[Order_ID]|Duplicate row fou...|  236|
|[Order_ID]|Duplicate row fou...|  260|
|[Order_ID]|Duplicate row fou...|  262|
|[Order_ID]|Duplicate row fou...|  289|
+----------+--------------------+-----+
only showing top 20 rows



# How many dropped rows?

In [28]:
df_cnt = df.count() 
cleaned_cnt = clean_df.count()
dropped_cnt = df_cnt - cleaned_cnt
print(f'''

source row count: {df_cnt}
cleaned row count: {cleaned_cnt}
dropped row count: {dropped_cnt}
error rate: {round(dropped_cnt * 100 / df_cnt, 2)}%   
      
      ''')



source row count: 128976
cleaned row count: 105819
dropped row count: 23157
error rate: 17.95%   
      
      
